# Lab 3 - Trichromacy/SVD, Regression

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.io import loadmat
from scipy.signal import gaussian
import random
random.seed(2)
%matplotlib notebook

## Part 1 Trichromacy

In this part of the lab, we will go over a simple trichromacy example. Let's remember how a trichromacy test works. Subjects are given a set of primaries and are asked to match the colors by adjusting the weights on a set of pre-determined primaries. Let's call the primaries $P$ and the test light $\vec{l}$. The humans will select the weights $\vec{w}$ such that $P\vec{w}$ produces a light that looks similar to $\vec{l}$. We'll denote this $P\vec{w} \sim \vec{l}$ 

We assume humans are some linear system $H$ - this matrix $H$ will take in a test light $\vec{l}$ and tell us how to weight the primaries. So $\vec{w} = H\vec{l}$. Putting this all together, we have $P\vec{w} = PH\vec{l} \sim \vec{l}$

In [ ]:
l = np.random.random(31)

We are given primaries and our human linear system $H$ below: 

In [ ]:
primaries = np.array([[3.72665317e-06, 4.57833362e-01, 4.39369336e-02],
       [1.86644691e-05, 6.06530660e-01, 1.11089965e-02],
       [8.36483472e-05, 7.54839602e-01, 2.18749112e-03],
       [3.35462628e-04, 8.82496903e-01, 3.35462628e-04],
       [1.20385999e-03, 9.69233234e-01, 4.00652974e-05],
       [3.86592014e-03, 1.00000000e+00, 3.72665317e-06],
       [1.11089965e-02, 9.69233234e-01, 2.69957850e-07],
       [2.85655008e-02, 8.82496903e-01, 1.52299797e-08],
       [6.57285286e-02, 7.54839602e-01, 6.69158609e-10],
       [1.35335283e-01, 6.06530660e-01, 2.28973485e-11],
       [2.49352209e-01, 4.57833362e-01, 6.10193668e-13],
       [4.11112291e-01, 3.24652467e-01, 6.10193668e-13],
       [6.06530660e-01, 2.16265167e-01, 2.28973485e-11],
       [8.00737403e-01, 1.35335283e-01, 6.69158609e-10],
       [9.45959469e-01, 7.95595087e-02, 1.52299797e-08],
       [1.00000000e+00, 4.39369336e-02, 2.69957850e-07],
       [9.45959469e-01, 2.27941809e-02, 3.72665317e-06],
       [8.00737403e-01, 1.11089965e-02, 4.00652974e-05],
       [6.06530660e-01, 5.08606923e-03, 3.35462628e-04],
       [4.11112291e-01, 2.18749112e-03, 2.18749112e-03],
       [2.49352209e-01, 8.83826307e-04, 1.11089965e-02],
       [1.35335283e-01, 8.83826307e-04, 4.39369336e-02],
       [6.57285286e-02, 2.18749112e-03, 1.35335283e-01],
       [2.85655008e-02, 5.08606923e-03, 3.24652467e-01],
       [1.11089965e-02, 1.11089965e-02, 6.06530660e-01],
       [3.86592014e-03, 2.27941809e-02, 8.82496903e-01],
       [1.20385999e-03, 4.39369336e-02, 1.00000000e+00],
       [3.35462628e-04, 7.95595087e-02, 8.82496903e-01],
       [8.36483472e-05, 1.35335283e-01, 6.06530660e-01],
       [1.86644691e-05, 2.16265167e-01, 3.24652467e-01],
       [3.72665317e-06, 3.24652467e-01, 1.35335283e-01]])

H = np.array([[-7.86629629e-03, -1.64055828e-02, -2.95981171e-02,
        -3.93796959e-02, -4.09500966e-02, -3.38263122e-02,
        -2.37004317e-02, -9.91485201e-03,  1.20239124e-02,
         3.57069852e-02,  6.48046756e-02,  1.04178973e-01,
         1.44668517e-01,  1.68752352e-01,  1.77676195e-01,
         1.74234972e-01,  1.60424243e-01,  1.37083289e-01,
         1.06634557e-01,  7.34436273e-02,  4.39069236e-02,
         2.20195756e-02,  8.79040897e-03,  2.16407666e-03,
        -5.16366094e-04, -1.13994950e-03, -8.66775757e-04,
        -5.47922896e-04, -3.41163670e-04, -1.58712800e-04,
        -1.06894912e-04],
       [ 3.18589820e-02,  6.65498781e-02,  1.21057897e-01,
         1.65625669e-01,  1.82539231e-01,  1.67568336e-01,
         1.46179420e-01,  1.26060988e-01,  8.45603935e-02,
         4.92830803e-02,  2.78158110e-02,  1.36406802e-02,
         2.84097397e-03, -2.50989671e-03, -5.22701906e-03,
        -6.80644635e-03, -6.62236256e-03, -6.79197033e-03,
        -5.95825114e-03, -4.92531575e-03, -3.87453776e-03,
        -2.91506416e-03, -2.10206731e-03, -1.40963160e-03,
        -9.04883888e-04, -5.42254762e-04, -3.06237143e-04,
        -1.59404323e-04, -8.40136175e-05, -4.06022050e-05,
        -1.99329051e-05],
       [ 2.71777556e-02,  5.62179675e-02,  1.00315960e-01,
         1.29839162e-01,  1.27729775e-01,  9.36612642e-02,
         4.66875314e-02, -1.36220201e-02, -8.72000273e-02,
        -1.55793381e-01, -2.33802345e-01, -3.27595055e-01,
        -3.87724450e-01, -3.65221662e-01, -2.79396978e-01,
        -1.43816136e-01,  3.56879942e-02,  2.48737645e-01,
         4.69506595e-01,  6.59391091e-01,  7.74562774e-01,
         7.85955117e-01,  6.97520716e-01,  5.36579177e-01,
         3.79600809e-01,  2.42798994e-01,  1.41234085e-01,
         7.53007753e-02,  4.06534560e-02,  1.95333127e-02,
         1.01241222e-02]])

Let's generate a new light that looks like our test_light, and plot it to compare it with the original light. Do they look alike?

In [ ]:
# TODO: use P, H, and our test light l to generate a new light combo
# that is "perceptually indistinguishable" from l, called matched_light
matched_light = #YOUR CODE HERE

# Do these lights have similar spectra? Plot l and matched_light to see
plt.plot(l, label = "Test Light")
plt.plot(matched_light, label = "Matched Light")
plt.ylabel("Intensity")
plt.xlabel("Wavelength (bins)")
plt.legend()

Print the weights for the matched light and the original test light. Are they the same?

In [ ]:
#TODO: find the weights associated with the test light, and the weights
#associated with the matched light
weights_for_test_light = #YOUR CODE HERE
weights_for_matched_light = #YOUR CODE HERE

print(weights_for_test_light)
print(weights_for_matched_light)

Let's take the SVD of $H$ - this will tell us what $H$ is doing "behind the scenes". How many singular values does $H$ have? Does that line up with what you expected?

In [ ]:
#TODO: take the SVD and display the number of singular values
U, S, Vt = #YOUR CODE HERE
number_of_singular_values = #YOUR CODE HERE
print(number_of_singular_values)

Now let's think about what information gets thrown away by our matrix $H$. Remember that the vectors that form the basis of the nullspace of $H$ are the vectors in $V$ that correspond with singular values of 0. Which vectors of V correspond with singular values of 0? How do we know they are in the nullspace?

In [ ]:
# TODO: list out the nullspace basis vectors using V and S
nullspace_basis_vectors = #YOUR CODE HERE

np.round(H @ nullspace_basis_vectors.T, 5)

Using this information, construct a new light $\vec{n}$ which is some weighted combination of basis vectors, and add it to your test light, $\vec{l}$. Show that these are metamers by demonstrating that $H\vec{n} = H\vec{l}$

In [ ]:
# TODO: generate some weighted combo of nullspace basis vectors and
# and add it to your test light
n = #YOUR CODE HERE

weights_for_new_light = #YOUR CODE HERE

print(weights_for_test_light)
print(weights_for_new_light)

Plot your new light and compare it with your old light. Is the new light a color that could be physically realizable? If not, try to find some other new light that is physically realizable and also is a metamer with the original test light.

In [ ]:

plt.plot(l, label = "Test Light")
plt.plot(n, label = "New Light")
#answers may vary
plt.plot(l + nullspace_basis_vectors[0], label = "(Physically realizable) New Light")
plt.ylabel("Intensity")
plt.xlabel("Wavelength (bins)")
plt.legend()

## Part 2 Regression

### Linear Regression: Visual Neuron

In this section, we will model the response of a simulated neuron responding to the luminance of a visual stimulus, and characterize its "spiking" with linear regression.

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.io import loadmat
import random
random.seed(2)

Create test data simulating a neuron firing in response to a light stimulus:

In [ ]:
# The response will have arbitrary units to represent input intensities
luminance = np.array([list(range(1,11))]).T

What is the spike response to different luminance? Model it as a linear amplification plus baseline and noise. Include a term to introduce experimental error to random trials.

In [ ]:
baseline, noise, amp = 10, 2, 2
experimentalError = (np.random.rand(10,1)>.5)*np.random.randn(10,1)*5
spikes = (amp * luminance + baseline + np.random.randn(len(luminance),1)*noise) + experimentalError 

In [ ]:
#plot luminance vs Spikes
f1, ax = plt.subplots(nrows=1, ncols=1)
plt.scatter(luminance, spikes, c = 'k',s = 100, ); 
plt.xlabel('Luminance'); plt.ylabel('Spikes')
plt.xlim([0, 11]); plt.ylim([0, max(spikes)[0]+10])

Find a value of beta (i.e., a slope of the regression line) such that when it's multiplied to each of the luminance values, we minimize the distance to the actual measurements (i.e., we look for $\beta_{opt}$ which minimizes $||\overrightarrow{y} - \beta_{Opt} *\overrightarrow{x}||^2$)

In [ ]:
#Find betaOpt (optimal beta) via SVD!
#Note that unlike MATLAB, when you do svd, it returns u, s, v; in Python, it returns u, s, v trasponsed!
betaOpt = #YOUR CODE HERE
print(betaOpt)

Now that we have our optimal weight to scale each luminance value, how well does our beta do at predicting the spikes? 

In [ ]:
#our prediction is multiplying each luminance value by beta
prediction = #YOUR CODE HERE
#get distance between measured spikes and our model prediction
predError = #YOUR CODE HERE
#get the squared distance
predErrorOpt = #YOUR CODE HERE
print(predErrorOpt)

In [ ]:
#Plot our prediction
f1, ax = plt.subplots(nrows=1, ncols=1)
plt.scatter(luminance, spikes, c = 'k',s = 100, )
plt.plot(luminance, prediction, c = 'k', lw = 3)
plt.xlabel('Luminance'); plt.ylabel('Spikes')
plt.xlim([0, 11]); plt.ylim([0, max(spikes)[0]+10])
plt.legend({'data', 'linear reg, squared error = %.4f' % predErrorOpt[0][0]})

Was this the best beta? Test a range of other beta values to confirm that your $\beta$ truly
minimizes $||\overrightarrow{y} - \beta_{Opt} * \overrightarrow{x}||^2$

In [ ]:
#Try 200 betas over a range of 0:2*betaOpt
numBeta = 200
testBetas = np.linspace(0, betaOpt[0][0]*2, numBeta)
#initialize 
sqrError = np.empty((1,numBeta))
for ii in range(numBeta):
    randomprediction = testBetas[ii]*luminance
    sqrError[0][ii] = (randomprediction-spikes).T @ (randomprediction-spikes)

In [ ]:
#now check if predErrorOpt is indeed optimal:
if min(sqrError[0]) >= predErrorOpt:
   #if the closest error you got by force was no smaller than your calculated beta opt....
   print('seems like we found a great solution')

In [ ]:
# Now plot the error for different betas
f2, ax = plt.subplots(nrows=1, ncols=1)
#plot the error of your set of test betas
plt.plot(testBetas,sqrError[0],c = 'b', lw = 3)
plt.plot([betaOpt[0][0], betaOpt[0][0]], [0, max(sqrError[0])], c ='r', lw = 2)
plt.xlabel('Beta'); plt.ylabel('Error metric')

### Multiple linear regression: visual neuron model with y-intercept

What if we would like to add a y-intercept? We can do this with multiple linear regression if we model our independent variable (x) as a matrix whose columns contain the x values of the first order polynomial 

$$y_{\text{Predicted}} = \beta_0* x_0 + \beta_1*x_1.$$ 

Solving this multiple linear regression will produce two beta values, $\beta_0$ (scaling the y intercept term) and Beta1 (scaling the slope of the regression line).

In [ ]:
#Create your regressor matrix and calculate the optimal betas with linear algebra
#create your "multivariate" data matrix X (containing x^0 and x^1 as columns)
X = #YOUR CODE HERE

In [ ]:
#Calculate betaOpt with the svd
betaOptYInt = #YOUR CODE HERE
print(betaOptYInt)

Now that we have our optimal weight to scale each luminance value, and our y-interecpt, how well does our beta (now a vector) do at predicting the spikes? 

In [ ]:
#our prediction is multiplying each luminance value by beta
predictionYInt = #YOUR CODE HERE
#get distance between measured spikes and our model prediction
predErrorYInt = #YOUR CODE HERE
#get the squared distance
predErrorOptYInt = #YOUR CODE HERE
print(predErrorOptYInt)

In [ ]:
#Plot our prediction with error val
f1, ax = plt.subplots(nrows=1, ncols=1)
plt.scatter(luminance, spikes, c = 'k',s = 100, )
plt.plot(luminance, prediction, c = 'k', lw = 3)
plt.plot(luminance, predictionYInt, c = 'r', lw = 3)
plt.xlabel('Luminance'); plt.ylabel('Spikes')
plt.xlim([0, 11]); plt.ylim([0, max(spikes)[0]+10])
plt.legend({'data', 'linear reg, squared error = %.4f' % predErrorOpt[0][0],
            'linear reg w/ y-int, squared error = %.4f' % predErrorOptYInt[0][0]})
plt.show()

How did our beta do? Test it agaist manually first, create a meshgrid of beta values (equivalent to a 2D version of the beta vector from the last section).

In [ ]:
nBetas = 100
beta0  = np.linspace(-betaOptYInt[0][0],betaOptYInt[0][0]*2, nBetas)
beta1  = np.linspace(1,betaOptYInt[1][0]*2, nBetas)

In [ ]:
#now compute the errors
allerr = np.empty((nBetas,nBetas))
for ii in range(nBetas):
    for jj in range(nBetas):
        bb = np.array([[beta0[ii],beta1[jj]]]).T
        sqrErr = (X @ bb- spikes).T @ (X @ bb- spikes)
        allerr[ii][jj] = sqrErr[0][0]

plot the contour and compare the old prediction error (without the y-int) with the new prediction error - did you do any better? what does it mean for our neuron that the model with the y-intercept has lower error?

In [ ]:
from mpl_toolkits.mplot3d import Axes3D  
fig3 = plt.figure()
ax = plt.axes(projection='3d')
betaX,betaY = np.meshgrid(beta0,beta1);
ax.plot_surface(betaX, betaY, allerr.T, cmap='viridis', edgecolor='none',alpha=0.5)

ax.scatter(betaOptYInt[0][0], betaOptYInt[1][0], predErrorOptYInt, c='r', marker='o')
ax.scatter(0, betaOpt, predErrorOpt, c ='b', marker='o')
ax.set_xlabel('X Label')
ax.set_ylabel('Y Label')
ax.set_zlabel('Z Label')


### Multiple linear regression: auditory neuron
Now let's try an example of multiple linear regression. The structure mult_linreg contains three fields: freq1, freq2 (the dB intensities of two frequencies of sound stimuli) and response, the response of an auditory neuron. 

In [ ]:
#First, load and plot the data ( in 3D!)
#add path if needed
import os
# path_str = ""
# path = path_str
# os.chdir(path)

x_raw = loadmat('mult_linreg.mat')
x = x_raw['data']
data_freq1,data_freq2,data_resp = np.array(x[0][0][0]), np.array(x[0][0][1]), np.array(x[0][0][2])

In [ ]:
fig5 = plt.figure()
ax = plt.axes(projection='3d')
ax.scatter(data_freq1, data_freq2, data_resp, c='b', marker='o')
ax.set_xlabel('Freq 1')
ax.set_ylabel('Freq 2')
ax.set_zlabel('Firing rate')


In [ ]:
#Perform linear regression
betaOpt = #YOUR CODE HERE
print(betaOpt)

In [ ]:
#Calculate error between the prediction frorm our model, and the measured values
#our prediction is multiplying each luminance value by beta
prediction = #YOUR CODE HERE
#get distance between measured spikes and our model prediction
predError = #YOUR CODE HERE
#get the squared distance
predErrorOpt = #YOUR CODE HERE

In [ ]:
#plot our linear model (it's a plane!)
x = np.linspace(0, max(data_freq1*1.2),100).T
y = np.linspace(0, max(data_freq2*1.2),100).T

xx, yy = np.meshgrid(x,y);
zz = betaOpt[0][0]*xx + betaOpt[1][0]*yy;

fig5 = plt.figure()
ax = plt.axes(projection='3d')
ax.scatter(data_freq1, data_freq2, data_resp, c='b', marker='o')
ax.plot_surface(xx,yy,zz, cmap='viridis', edgecolor='none',alpha=0.5)
ax.set_xlabel('Freq 1')
ax.set_ylabel('Freq 2')
ax.set_zlabel('Firing rate')

In [ ]:
#Was this the best beta?
#first, create vectors of your possible betas
nBetas = 200

beta0 = np.linspace(0,betaOpt[0]*2,nBetas)
beta1 = np.linspace(0,betaOpt[1]*2,nBetas)

#now compute the errors
allerr = np.empty((nBetas,nBetas))
for ii in range(nBetas):
    for jj in range(nBetas):
        bb = np.array([[beta0[ii][0], beta1[jj][0]]]).T
        sqrErr = (data_freq1_2 @ bb - data_resp).T @ (data_freq1_2 @ bb- data_resp)
        allerr[ii][jj] = sqrErr[0][0]


In [ ]:
fig6 = plt.figure()
ax = plt.axes(projection='3d')
betaX, betaY = np.meshgrid(beta0,beta1)
ax.plot_surface(betaX, betaY,allerr.T, cmap='viridis', edgecolor='none',alpha=0.5)
ax.scatter(betaOpt[0][0], betaOpt[1][0], predErrorOpt, c='r', marker='o')
ax.set_xlabel('Freq 1')
ax.set_ylabel('Freq 2')
ax.set_zlabel('Firing rate')

### Multiple Linear Regression: Auditory neuron with baseline firing

What if we suspect the auditory neuron has some baseline firing rate? We might want to include an intercept term in our regression. We can do this the same way we added an intercept term to the standard linear regression: by adding an $x_0$ term to our linear regression.

In [ ]:
#Linear Regression 
newX = #YOUR CODE HERE
betaOpt = #YOUR CODE HERE
print(betaOpt)

In [ ]:
#Calculate error between the prediction from our model, and the measured values
prediction = #YOUR CODE HERE
#get distance between measured spikes and our model prediction
predError = #YOUR CODE HERE
#get the squared distance
predErrorOpt = #YOUR CODE HERE

In [ ]:
#plot our linear model (it's a plane!)
newBeta0 = np.linspace(0, max(data_freq1)*1.2,nBetas).T
newBeta1 = np.linspace(0, max(data_freq2)*1.2,nBetas).T

newBetaX,newBetaY = np.meshgrid(newBeta0,newBeta1);
newS = betaOpt[0][0]*np.ones(newBetaX.shape)+ betaOpt[1][0]*newBetaX + betaOpt[2][0]*newBetaY


fig7 = plt.figure()
ax = plt.axes(projection='3d')
ax.scatter(data_freq1, data_freq2, data_resp, c='b', marker='o')
ax.plot_surface(newBetaX,newBetaY,newS, cmap='viridis', edgecolor='none',alpha=0.5)
